In [1]:
import json
import numpy as np
import pandas as pd
from tqdm import tqdm
import sklearn
from sklearn.metrics import f1_score, accuracy_score
from sklearn.model_selection import KFold, StratifiedKFold
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
import optuna.integration.lightgbm as lgb

In [2]:
all_new = pd.read_csv('data/feature_df_agg_svd16.csv')
BERT_svd256 = pd.read_csv("data/BERT_svd256.csv")
ALBERT_svd256 = pd.read_csv("data/ALBERT_svd256.csv")
ROBERTA_svd256 = pd.read_csv("data/ROBERTA_svd256.csv")
XLMROBERTA_svd256 = pd.read_csv("data/XLMROBERTA_svd256.csv")
tfidf_svd_raw_128 = pd.read_csv("data/tfidf_svd_raw_128_2gram.csv")
mfw_df = pd.read_csv('data/mfw.csv')
miw_df = pd.read_csv('data/miw.csv')

In [3]:
all_new = pd.merge(all_new, BERT_svd256, on="id", how="outer")
all_new = pd.merge(all_new, ALBERT_svd256, on="id", how="outer")
all_new = pd.merge(all_new, ROBERTA_svd256, on="id", how="outer")
all_new = pd.merge(all_new, XLMROBERTA_svd256, on="id", how="outer")
all_new = pd.merge(all_new, tfidf_svd_raw_128, on="id", how="outer")
all_new = pd.merge(all_new, miw_df, on="id", how="outer")
all_new = pd.merge(all_new, mfw_df, on="id", how="outer")

In [4]:
def run_optuna_lgbm(test, train, target_cols, feature_cols, categorical_cols, seed):
    """
    import optuna.integration.lightgbm as lgb
    """
    X_train = train[feature_cols]
    y_train = train[target_cols]
    X_test = test[feature_cols]
    
    y_preds = []
    models = []
    oof_train = np.zeros((len(X_train),))
    importances = []
    
    params = {
        'objective': 'binary',
        'metric': 'binary_logloss',
    }
    
    #cv = KFold(n_splits=5, shuffle=True, random_state=0)
    cv = StratifiedKFold(n_splits=7, shuffle=True, random_state=seed)
    for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train, X_train["category2"])):
        X_tr = X_train.iloc[train_index]
        X_val = X_train.iloc[valid_index]
        y_tr = y_train.iloc[train_index]
        y_val = y_train.iloc[valid_index]

        lgb_train = lgb.Dataset(X_tr,
                                y_tr,
                                categorical_feature=categorical_cols)

        lgb_eval = lgb.Dataset(X_val,
                               y_val,
                               reference=lgb_train,
                               categorical_feature=categorical_cols)
        
        model = lgb.train(params,
                          lgb_train,
                          valid_sets=[lgb_train, lgb_eval],
                          verbose_eval=False,
                          num_boost_round=1000,
                          early_stopping_rounds=10,
                          )
        
        oof_train[valid_index] = model.predict(X_val,
                                               num_iteration=model.best_iteration)
        y_pred = model.predict(X_test,
                               num_iteration=model.best_iteration)

        y_preds.append(y_pred)
        models.append(model)
        
        
        # display importance
        importance = pd.DataFrame(model.feature_importance(), index=X_test.columns, columns=['importance'])
        display(importance)
        importances.append(importance)

    return oof_train, sum(y_preds) / len(y_preds), importances

In [5]:
test_set = all_new[all_new["data_type"] == "test"]
train_set = all_new[all_new["data_type"] == "train"]


with open("data/base_feature_config_lgmb.json") as f:
    feature_config = json.load(f)
base_features = feature_config["selected_feature"]
base_features.extend(list(mfw_df.columns.drop("id")))
base_features.extend(list(miw_df.columns.drop("id")))

TARGET_COLS = ["state"]
CATEGORICAL_COLS = [
    "country",
    "category1",
    "category2",
    "country+category1",
    "country+category2",
    "category1+category2",
]

for category in set(CATEGORICAL_COLS):
    if category not in base_features:
        CATEGORICAL_COLS.remove(category)
        print(f"{category} is not included in base_features")

category1 is not included in base_features


In [6]:
def run_lgbm_models(test_set, train_set, target_cols, base_features, categorical_cols):
    
    additional_features = [
        (list(BERT_svd256.columns.drop("id")), "BERT"),
        (list(ALBERT_svd256.columns.drop("id")), "ALBERT"),
        (list(ROBERTA_svd256.columns.drop("id")), "ROBERTA"),
        (list(XLMROBERTA_svd256.columns.drop("id")), "XLMROBERTA"),
        (list(tfidf_svd_raw_128.columns.drop("id")), "tfidf"),
        (list(tfidf_svd_raw_128.columns.drop("id")) + list(BERT_svd256.columns.drop("id")), "tfidf+BERT"),
        (list(tfidf_svd_raw_128.columns.drop("id")) + list(ALBERT_svd256.columns.drop("id")), "tfidf+ALBERT"),
        (list(tfidf_svd_raw_128.columns.drop("id")) + list(ROBERTA_svd256.columns.drop("id")), "tfidf+ROBERTA"),
        (list(tfidf_svd_raw_128.columns.drop("id")) + list(XLMROBERTA_svd256.columns.drop("id")), "tfidf+XLMROBERTA"),
    ]
    
    for n, additional_feature in enumerate(additional_features):
        additional_feature, feature_name = additional_feature
        print(f"============ {feature_name} training ============")
        feature_cols = base_features + additional_feature
        
        oof, preds, importances = run_optuna_lgbm(test_set,
                                                  train_set,
                                                  target_cols,
                                                  feature_cols,
                                                  categorical_cols,
                                                  seed=n*2021
                                                 )
        config_dict = {
        "selected_feature": feature_cols,
        "out_of_fold": list(oof),
        "prediction": list(preds),
            "seed": n*2021,
        }
        with open(f"data/lgbm_{feature_name}_seed2021.json", 'w') as f:
            json.dump(config_dict, f)

In [7]:
#　約２時間
run_lgbm_models(test_set, train_set, TARGET_COLS, base_features, CATEGORICAL_COLS)

/home/teppei/anaconda3/lib/python3.8/site-packages/sklearn/model_selection/_split.py:670: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=7.
  warnings.warn(("The least populated class in y has only %d"
[I 2021-01-29 15:30:09,824] A new study created in memory with name: no-name-bff4a3a5-f69d-4673-b42b-e2872e36c96a
feature_fraction, val_score: inf:   0%|          | 0/7 [00:00<?, ?it/s]

============ BERT training ============
[LightGBM] [Info] Number of positive: 4554, number of negative: 4484


/home/teppei/anaconda3/lib/python3.8/site-packages/lightgbm/basic.py:1551: UserWarning: Using categorical_feature in Dataset.
  warnings.warn('Using categorical_feature in Dataset.')


[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.037760 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 120400
[LightGBM] [Info] Number of data points in the train set: 9038, number of used features: 501
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.503873 -> initscore=0.015490
[LightGBM] [Info] Start training from score 0.015490


/home/teppei/anaconda3/lib/python3.8/site-packages/lightgbm/basic.py:1286: UserWarning: Overriding the parameters from Reference Dataset.
  warnings.warn('Overriding the parameters from Reference Dataset.')
/home/teppei/anaconda3/lib/python3.8/site-packages/lightgbm/basic.py:1098: UserWarning: categorical_column in param dict is overridden.
  warnings.warn('{} in param dict is overridden.'.format(cat_alias))
feature_fraction, val_score: 0.419807:  14%|#4        | 1/7 [00:00<00:05,  1.08it/s]

...

[LightGBM] [Info] Number of positive: 4566, number of negative: 4473
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.059440 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 153032
[LightGBM] [Info] Number of data points in the train set: 9039, number of used features: 629
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.505144 -> initscore=0.020578
[LightGBM] [Info] Start training from score 0.020578


min_data_in_leaf, val_score: 0.406978:  80%|########  | 4/5 [00:11<00:02,  2.89s/it]

[LightGBM] [Info] Number of positive: 4566, number of negative: 4473
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.051903 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 153032
[LightGBM] [Info] Number of data points in the train set: 9039, number of used features: 629
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.505144 -> initscore=0.020578
[LightGBM] [Info] Start training from score 0.020578


min_data_in_leaf, val_score: 0.406978: 100%|##########| 5/5 [00:14<00:00,  2.83s/it]


importance
country                      1
duration                     0
category2                   98
number_of_<i>                1
number_of_</i>              10
...                        ...
XLMROBERTA_svd_251           5
XLMROBERTA_svd_252           7
XLMROBERTA_svd_253           7
XLMROBERTA_svd_254          13
XLMROBERTA_svd_255           2

[629 rows x 1 columns]